In [ ]:
%matplotlib inline

In [ ]:
import IPython.display as ipd
import sys
import io
import numpy as np
import pandas as pd
import matplotlib as mpl
import matplotlib.pyplot as plt
import scipy.stats as sps

Global information
===

In [ ]:
mpl.rcParams["font.family"] = "TeX Gyre Pagella"
mpl.rcParams["font.size"] = 8
rst_column_width = 3.3
rst_total_width = 7

In [ ]:
deaf_pups = {"b3", "b5", "b8"}
hearing_pups = {"b2", "b4", "b7"}
all_pups = deaf_pups.union(hearing_pups)

In [ ]:
group_colors = dict(hearing="#7bb992", deaf="#5f0f00")
bat_colors = {**{bat: group_colors["deaf"] for bat in deaf_pups},
              **{bat: group_colors["hearing"] for bat in hearing_pups}}
bat_markers = dict(zip(sorted(all_pups), ["P", "o", "*", "s", "X", "D"]))

Load data for juveniles
===

In [ ]:
pup_sessions = pd.read_csv("../pup_sessions.csv", index_col=0, parse_dates=["start_time"],
                           dtype=dict(before_deafening=np.bool))
pup_calls = pd.read_csv("../pup_calls.csv", index_col=[0, 1], parse_dates=["start_time"], na_values=["--"],
                        dtype=dict(calling_bat_deaf=np.bool, calling_bat_mother=np.bool, before_deafening=np.bool))

# filter out mother vocalisations
pup_calls = pup_calls[~pup_calls["calling_bat_mother"]].reset_index()

In [ ]:
bat_birthdates = pd.DataFrame([("b2", "2017/01/26"),
                               ("b4", "2017/01/30"),
                               ("b7", "2017/02/08"),
                               ("b3", "2017/01/29"),
                               ("b5", "2017/02/02"),
                               ("b8", "2017/02/08")], columns=["bat", "birthdate"])
bat_birthdates["birthdate"] = pd.to_datetime(bat_birthdates["birthdate"])
bat_birthdates.set_index("bat", inplace=True)

In [ ]:
# determine ages (in full days) of the calling bats

birth_dates = bat_birthdates.loc[pup_calls["calling_bat"]]["birthdate"].reset_index(drop=True)
ages = pup_calls["start_time"] - birth_dates
pup_calls["calling_bat_age_in_days"] = ages.dt.days
pup_calls["calling_bat_age_in_weeks"] = ages.dt.days // 7
pup_calls["call_rms"] = pup_calls["call_rms"] + 55

Load data for adults
===

In [ ]:
def single_value(values):
    value_set = set(values)
    if len(value_set) != 1:
        raise ValueError("non-unity set")
    return next(iter(value_set))

In [ ]:
adult_calls = pd.read_csv("../adult_calls.csv",
                          parse_dates=["start_time"],
                          na_values=["--"],
                          dtype=dict(calling_bat_deaf=np.bool, session_id=np.int),
                          index_col=["session_id", "call_id"])
adult_calls["recording_day"] = adult_calls["start_time"].dt.date
adult_calls["call_rms"] -= adult_calls["call_rms"].min()
adult_calls["group"] = np.where(adult_calls["calling_bat_deaf"], "deaf", "hearing")

adult_sessions = pd.read_csv("../adult_sessions.csv",
                             parse_dates=["start_time"],
                             dtype=dict(group="category"),
                             index_col=0)

adult_recording_days = adult_sessions[["group"]].groupby(adult_sessions["start_time"].dt.date).agg(single_value)
adult_recording_days.index.name = "recording_day"

Data to be dropped
===

Possible echolocation calls (3 ms or shorter)
---

In [ ]:
pup_calls = pup_calls[pup_calls["call_duration"] > 3e-3]
adult_calls = adult_calls[adult_calls["call_duration"] > 3e-3]

Sessions shorter than 20 minutes
---

In [ ]:
session_gaps = pup_sessions.sort_values("start_time")["start_time"].diff()
new_index = session_gaps.index.insert(0, -1)
new_index = new_index[:-1]
session_gaps.index = new_index
session_gaps.drop(-1, inplace=True)

In [ ]:
ids_to_drop = session_gaps[session_gaps < pd.Timedelta(20, "m")].index

In [ ]:
pup_calls = pup_calls[~pup_calls["session_id"].isin(ids_to_drop)]
pup_sessions = pup_sessions.drop(ids_to_drop)

Last two recordings with mother for pups that have more than others
---

In [ ]:
sorted_pup_mother_sessions = pup_sessions[pup_sessions["animal2"].str.startswith("m")].sort_values("start_time")
session_counts_with_mothers = sorted_pup_mother_sessions["animal1"].value_counts()
num_sessions_to_drop = session_counts_with_mothers - session_counts_with_mothers.min()

ids_to_drop = set()
for bat, drop_count in num_sessions_to_drop.iteritems():
    if drop_count == 0:
        continue
    this_bat_sessions = sorted_pup_mother_sessions[sorted_pup_mother_sessions["animal1"] == bat]
    ids_to_drop = ids_to_drop.union(this_bat_sessions.tail(drop_count).index)

pup_calls = pup_calls[~pup_calls["session_id"].isin(ids_to_drop)]
pup_sessions = pup_sessions.drop(index=ids_to_drop)

Compute activity statistics (separately for pups before and after deafening)
===

In [ ]:
calls_per_pup_and_session = pup_calls.reset_index().groupby(["calling_bat", "session_id"])[["calling_bat"]].count() / (20*6) # per 10 seconds
calls_per_pup_and_session.columns = ["calls_per_10s"]
calls_per_pup_and_session.reset_index(inplace=True)

session_dates = pup_sessions.loc[calls_per_pup_and_session["session_id"]]["start_time"]
birth_dates = bat_birthdates.loc[calls_per_pup_and_session["calling_bat"]]["birthdate"]
calls_per_pup_and_session["calling_bat_age_in_days"] = \
    (session_dates.reset_index(drop=True) - birth_dates.reset_index(drop=True)).dt.days
calls_per_pup_and_session["calling_bat_age_in_weeks"] = \
    calls_per_pup_and_session["calling_bat_age_in_days"] // 7
calls_per_pup_and_session = pd.merge(calls_per_pup_and_session, pup_sessions[["before_deafening"]],
                                     left_on="session_id", right_index=True,)

In [ ]:
dfs = []

for before_deafening in [False, True]:
    mask = pup_calls["before_deafening"]
    if not before_deafening:
        mask = ~mask
    gr = pup_calls[mask].groupby(["calling_bat", "calling_bat_age_in_weeks"])
    gr = gr[["call_duration", "mean_aperiodicity", "f0_mean", "call_rms"]]
    params_per_pup_and_week = gr.median()
    params_per_pup_and_week["calls_this_week"] = gr.size()
    
    mask = calls_per_pup_and_session["before_deafening"]
    if not before_deafening:
        mask = ~mask
    gr = calls_per_pup_and_session[mask].groupby(["calling_bat", "calling_bat_age_in_weeks"])
    params_per_pup_and_week["calls_per_10s"] = gr["calls_per_10s"].mean()
    params_per_pup_and_week.reset_index(inplace=True)
    params_per_pup_and_week["before_deafening"] = before_deafening
    
    dfs.append(params_per_pup_and_week)
    
params_per_pup_and_week = pd.concat(dfs)

In [ ]:
gr = adult_calls.groupby(["group", "session_id"], observed=True)
calls_per_adult_group_and_session = gr.size().to_frame(name="calls_per_10s").reset_index()

Quantities of extracted data
===

In [ ]:
print("Total calls by pups: {}\nCalls by deaf pups: {} ({:.1f} %)\nCalls by hearing pups: {} ({:.1f} %)".format(
        len(pup_calls),
        np.sum(pup_calls["calling_bat_deaf"]),
        np.sum(pup_calls["calling_bat_deaf"]) / len(pup_calls) * 100,
        np.sum(~pup_calls["calling_bat_deaf"]),
        np.sum(~pup_calls["calling_bat_deaf"] / len(pup_calls) * 100)))

In [ ]:
print("Total calls by adults: {}\nCalls by deaf adults: {} ({:.1f} %)\nCalls by hearing adults: {} ({:.1f} %)".format(
        len(adult_calls),
        np.sum(adult_calls["calling_bat_deaf"]),
        np.sum(adult_calls["calling_bat_deaf"]) / len(adult_calls) * 100,
        np.sum(~adult_calls["calling_bat_deaf"]),
        np.sum(~adult_calls["calling_bat_deaf"] / len(adult_calls) * 100)))

Main figure
===

In [ ]:
def plot_trajectories(ax, values, parameter, scale):
    line_artists = {}
    for bat, df in values.groupby("calling_bat"):
        bat_color, bat_marker = bat_colors[bat], bat_markers[bat]
        line_artist, = ax.plot(df["calling_bat_age_in_weeks"] + 1, df[parameter] * scale,
                               c=bat_color, linewidth=0.8)
        ax.plot(df["calling_bat_age_in_weeks"] + 1, df[parameter] * scale,
                c=bat_color, marker=bat_marker, markersize=5, clip_on=False,
                markerfacecolor="none", linestyle="")
        line_artists[bat] = line_artist
    return line_artists

In [ ]:
def plot_histograms(ax, values, parameter, scale, y_range):
    data = {}

    if "group" in values:
        for group, hearing in [("deaf", False), ("hearing", True)]:
            data[hearing] = (values.loc[values["group"] == group, parameter] * scale).values
    else:
        for hearing, df in values.groupby(values["calling_bat"].isin(hearing_pups)):
            data[hearing] = (df[parameter] * scale).values

    ax.hist([data[True], data[False]], density=True,
            range=y_range, bins=15,
            color=[group_colors["hearing"], group_colors["deaf"]],
            orientation="horizontal", rwidth=0.85)

In [ ]:
def plot_boxplots(ax, values, parameter, scale, test_significance=False):
    data = []
    for group in ["deaf", "hearing"]:
        data.append(scale * values.loc[values["group"] == group, parameter].dropna().values)

    artists = boxplot_ax.boxplot(data, vert=True, manage_ticks=False, showfliers=False, widths=0.75,
                                 patch_artist=True,
                                 boxprops=dict(linewidth=0.5),
                                 whiskerprops=dict(linewidth=0.5),
                                 medianprops=dict(linewidth=1, color="bisque"),
                                 capprops=dict(linewidth=0.5))

    artists["boxes"][0].set_facecolor(group_colors["deaf"])
    artists["boxes"][1].set_facecolor(group_colors["hearing"])
    
    if test_significance:
        p = sps.mannwhitneyu(data[0], data[1], alternative="two-sided").pvalue
        if p < 0.05:
            ax.annotate("*", (0.8, 0.8), xycoords="axes fraction")

In [ ]:
call_parameters = [("calls_per_10s", 1, "Vocal activity\n[calls/10 s]", (0, 100), 20),
                   ("call_rms", 1, "Amplitude\n[dB]", (0, 54), 12),
                   ("call_duration", 1e3, "Duration\n[ms]", (0, 80), 20),
                   ("f0_mean", 1e-3, "Fundamental\nfrequency [kHz]", (0, 40), 10),
                   ("mean_aperiodicity", 1, "Aperiodicity\n[1]", (0, 1), 0.25)]

fig_width = rst_total_width
fig_height = 0.7 * fig_width
left_margin, right_margin = 0.75, 0.1
bottom_margin, top_margin = 0.45, 0.45
spacing = 0.2
boxplot_extra_spacing = 0.1

row_height = (fig_height - bottom_margin - top_margin - (len(call_parameters) - 1) * spacing) / len(call_parameters)
trajectory_width = 3.2
boxplot_width = 0.2
histogram_width = (fig_width - left_margin - right_margin - trajectory_width - boxplot_width - 4 * spacing - boxplot_extra_spacing) / 3

fig = plt.figure(figsize=(fig_width, fig_height))

roman_numerals = ["I", "II", "III", "IV", "V"]

for i, (parameter, scale, y_label, y_range, y_tick_interval) in enumerate(reversed(call_parameters)):
    early_ax = \
        fig.add_axes([left_margin / fig_width,
                      (bottom_margin + i * (row_height + spacing)) / fig_height,
                      histogram_width / fig_width,
                      row_height / fig_height])
    late_ax = \
        fig.add_axes([(left_margin + histogram_width + spacing) / fig_width,
                      (bottom_margin + i * (row_height + spacing)) / fig_height,
                      histogram_width / fig_width,
                      row_height / fig_height])
    adult_ax = \
        fig.add_axes([(left_margin + 2 * (histogram_width + spacing)) / fig_width,
                      (bottom_margin + i * (row_height + spacing)) / fig_height,
                      histogram_width / fig_width,
                      row_height / fig_height])
    trajectory_ax = \
        fig.add_axes([(left_margin + 3 * (histogram_width + spacing)) / fig_width,
                      (bottom_margin + i * (row_height + spacing)) / fig_height,
                      trajectory_width / fig_width,
                      row_height / fig_height])
    boxplot_ax = \
        fig.add_axes([(left_margin + 3 * histogram_width + trajectory_width + 4 * spacing + boxplot_extra_spacing) / fig_width,
                      (bottom_margin + i * (row_height + spacing)) / fig_height,
                      boxplot_width / fig_width,
                      row_height / fig_height])
    overall_ax = \
        fig.add_axes([left_margin / fig_width,
                      (bottom_margin + i * (row_height + spacing)) / fig_height,
                      (fig_width - left_margin - right_margin) / fig_width,
                      row_height / fig_height], frameon=False)
    overall_ax.set_xticks([])
    overall_ax.set_yticks([])
    
    if parameter == "calls_per_10s":
        df = calls_per_pup_and_session
    else:
        df = pup_calls
    plot_histograms(early_ax,
                    df.query("before_deafening"),
                    parameter, scale, y_range)
    plot_histograms(late_ax,
                    df.query("not before_deafening"),
                    parameter, scale, y_range)
    
    if parameter == "calls_per_10s":
        df = calls_per_adult_group_and_session
    else:
        df = adult_calls
    plot_histograms(adult_ax, df,
                    parameter, scale, y_range if parameter != "calls_per_10s" else (0, 400))
    
    plot_trajectories(trajectory_ax,
                      params_per_pup_and_week.query("not before_deafening and calling_bat_age_in_weeks <= 24"),
                      parameter, scale)
    
    trajectory_ax.xaxis.set_major_locator(mpl.ticker.MultipleLocator(4))
    trajectory_ax.set_xlim(2, 25)
    trajectory_ax.spines["left"].set_position(("outward", 3))

    plot_boxplots(boxplot_ax, df, parameter, scale, test_significance=True)
    boxplot_ax.set_xlim(0.25, 2.75)
    
    if i == 0:
        trajectory_ax.set_xlabel("Week of age")
        trajectory_ax.xaxis.set_major_formatter(mpl.ticker.FuncFormatter(lambda x, pos: "{}th".format(int(x))))
        #trajectory_ax.xaxis.set_label_coords(0.5, -0.4)
    else:
        for ax in [early_ax, late_ax, trajectory_ax]:
            ax.set_xticklabels([])
            
    if i == len(call_parameters) - 1:
        early_ax.set_title("a)\n\n< 2 weeks", fontsize=8)
        late_ax.set_title("b)\n\n2–25 weeks", fontsize=8)
        adult_ax.set_title("c)\n\n2 years", fontsize=8)
        boxplot_ax.set_title("e)\n\n2 years", fontsize=8)
        trajectory_ax.set_title("d)\nDevelopment trajectory of median parameter values\nat 2–25 weeks of age", fontsize=8)
        early_ax.annotate("hearing",
                         xy=(0, 1), xycoords="axes fraction",
                         xytext=(5, -10), textcoords="offset points",
                         verticalalignment="top", horizontalalignment="left",
                         color=group_colors["hearing"])
        early_ax.annotate("deafened",
                         xy=(0, 1), xycoords="axes fraction",
                         xytext=(5, 0), textcoords="offset points",
                         verticalalignment="top", horizontalalignment="left",
                         color=group_colors["deaf"])
            
    for ax in [early_ax, late_ax, adult_ax, trajectory_ax, boxplot_ax]:
        if ax is adult_ax and parameter == "calls_per_10s":
            ax.set_ylim(0, 400)
            ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(100))
        else:
            ax.set_ylim(y_range[0], y_range[1])
            ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(y_tick_interval))

        for spine in ["right", "top"]:
            ax.spines[spine].set_visible(False)
        ax.spines["bottom"].set_position(("outward", 3))
            
    for ax in [late_ax, adult_ax, trajectory_ax, boxplot_ax]:
        if (ax is not adult_ax or parameter != "calls_per_10s") \
                and (ax is not trajectory_ax or parameter != "calls_per_10s"):
            ax.set_yticklabels([])
        
    for ax in [early_ax, late_ax, adult_ax, boxplot_ax]:
        ax.set_xticks([])
        ax.spines["bottom"].set_visible(False)
        
    early_ax.set_ylabel(y_label)
    early_ax.yaxis.set_label_coords(-0.32 / histogram_width, 0.5)
    
    overall_ax.set_ylabel(roman_numerals[-i - 1],
                          rotation="0",
                          verticalalignment="center",
                         labelpad=49)
    
fig.savefig("../parameters.pdf")

Parameter table
===

In [ ]:
per_session_parameters = [("call_rms", 1, "Amplitude [dB]"),
                          ("call_duration", 1e3, "Duration [ms]"),
                          ("f0_min", 1e-3, "Minimum fundamental frequency [kHz]"),
                          ("f0_mean", 1e-3, "Mean fundamental frequency [kHz]"),
                          ("f0_max", 1e-3, "Maximum fundamental frequency [kHz]"),
                          ("f0_start", 1e-3, "Fundamental frequency at call onset [kHz]"),
                          ("f0_end", 1e-3, "Fundamental frequency at end of call [kHz]"),
                          ("f_min", 1e-3, "Minimum frequency [kHz]"),
                          ("f_max", 1e-3, "Maximum frequency [kHz]"),
                          ("bandwidth", 1e-3, "Bandwidth [kHz]"),
                          ("spectral_centroid", 1e-3, "Spectral centroid frequency [kHz]"),
                          ("mean_aperiodicity", 1, "Aperiodicity [1]")]

In [ ]:
adult_calls.loc[:, "bandwidth"] = adult_calls["f_max"] - adult_calls["f_min"]
def q25(series):
    return series.quantile(0.25)
def q75(series):
    return series.quantile(0.75)

adult_groups = adult_calls[[p[0] for p in per_session_parameters] + ["group"]].groupby("group")
adult_summary = adult_groups.agg([q25, "median", q75])

In [ ]:
per_session_parameters.insert(0, ("calls_per_10s", 1, "Vocal activity [calls/10 s]"))
adult_activity_summary = calls_per_adult_group_and_session.groupby("group")[["calls_per_10s"]].agg([q25, "median", q75])
adult_summary = pd.concat([adult_activity_summary, adult_summary], axis=1)

In [ ]:
fout = io.StringIO()
print("<!DOCTYPE html><body><table>", file=fout)
print("<tr><th></th><th colspan='3'>Hearing (N={})</th><th colspan='3'>Deaf (N={})</th></tr>".format(*adult_calls["group"].value_counts().loc[["hearing", "deaf"]]), file=fout)
print("<tr><th></th>{}<th>p &lt; 0.05 (Mann–Whitney)</th></tr>".format("<th>Q25</th><th>Q50</th><th>Q75</th>" * 2), file=fout)

for parameter_name, scale, parameter_description in per_session_parameters:
    print("<tr><th>{}</th>".format(parameter_description), file=fout, end="")
    test_data = []
    for group in ["hearing", "deaf"]:
        for statistic in ["q25", "median", "q75"]:
            print("<td>{:.2f}</td>".format(adult_summary.loc[group, (parameter_name, statistic)] * scale), file=fout, end="")
        if parameter_name != "calls_per_10s":
            test_data.append(adult_calls.loc[adult_calls["group"] == group, parameter_name].values)
    if not test_data:
        print("<td>(see plot)</td>", file=fout)
    else:
        p = sps.mannwhitneyu(test_data[0], test_data[1], alternative="two-sided").pvalue
        if p < 0.05:
            print("<td>*</td>".format(p), file=fout)
        else:
            print("<td>{:.2f}</td>".format(p), file=fout)
    print("</tr>", file=fout)
print("</table></body>", file=fout)

parameters_table = fout.getvalue()

In [ ]:
ipd.display(ipd.HTML(parameters_table))
with open("../parameters_table.html", "wt") as fout:
    print(parameters_table, file=fout, end="")